In [36]:
using CSV, DataFrames, Plots, Statistics, StatsBase, JLD, Dates

include("Mods.jl");

datapath = "../Data/Stage0/";

theme(:dark)
Plots.default(titlefontsize=12, tickfontsize=10, labelfontsize=12, legendfontsize=9,
    fontfamily="Computer Modern", frame=:box, label=nothing)
plotlyjs();

In [82]:
Data = CSV.read(datapath * "Data_Cleared.csv", DataFrame)
delete!(Data, findall(x -> x == 0, Data.TotalPrice))
sort!(Data, "Date")
Data.Group = parse.(Int, getindex.(split.(Data[:, 1], "-"), 1))
Data.Product = parse.(Int, getindex.(split.(Data[:, 1], "-"), 2))
Data.Price = Data.TotalPrice ./ Data.Quantity
Data.NumDate = CostumMods.ConvertDate.(Data.Date)
Data.Date = CostumMods.ConvertToDateTime.(Data.NumDate)
CSV.write(datapath * "Data_0.csv", select!(Data, Not([:Category, :Quantity, :TotalPrice])));

In [92]:
ProdsName = sort(collect(Set(Data.Product)))
SelectedDates = []
SelectedProds = []
StdList = []
PLT1 = begin
    plot()
    for Prod in ProdsName
        dates = Data.NumDate[findall(x -> x == Prod, Data.Product)]
        if minimum(dates) < 500 && maximum(dates) > 1500 && length(Set(dates)) > 50 && Prod ∉ [41, 30]
            scatter!(dates, fill(Prod, length(dates)), label=nothing, msw=0, ms=0.5)
            push!(SelectedDates, length(dates))
            push!(SelectedProds, Prod)
            push!(StdList, std(dates))
        end
    end
    plot!()
end

PLT2 = begin
    histogram([Data.NumDate[findall(x -> x == Prod, Data.Product)] for Prod ∈ ProdsName],
        bins = 100, alpha = 0.25)
    plot!(xlab = "nth day", ylab = "Count of trades", title = "Histogram of trades dates", size = (1000, 800))
end

# display(PLT1)
display(PLT2)

In [96]:
CountProds = Int[]
for day ∈ 1:2200
    for Prod ∈ ProdsName
        if day ∈ Data.NumDate[findall(x -> x == Prod, Data.Product)]
            push!(CountProds, day)
        end
    end
end
histogram(CountProds, bins = 100)

In [20]:
ProdsName = sort(collect(Set(Data.Product)))
SelectedProds = []
for Prod ∈ ProdsName
    df = Data[findall(x -> x == Prod, Data.Product), :]
    if minimum(df.Date) < 500 && maximum(df.Date) > 1500 && length(Set(df.Date)) > 50 && Prod ∉ [41, 30]
        push!(SelectedProds, "$(CostumMods.GroupToProduct(Prod))-$Prod")
        CSV.write(SelectedDataPath * "$(CostumMods.GroupToProduct(Prod))-$Prod.csv", select(df, Not([:Group, :Product])))
    end
end

save(datapath * "SelectedData/SelectedProds.jld", "SelectedProds", sort(SelectedProds))